In [1]:
from hazm import *
import openpyxl
from pathlib import Path
import collections
import math
import itertools
import random
import numpy as np
from tqdm import tqdm
import heapq as hq
import csv
import pickle

In [2]:
N_documents = 0
normalizer = Normalizer()
stemmer = Stemmer()
tokens = []
doc_classes = {}
doc_vectors = {}
doc_tf = {}
links = {}

In [3]:

xlsx_file = Path('IR00_3_11k News.xlsx')
wb_obj = openpyxl.load_workbook(xlsx_file)
sheet = wb_obj.active


In [3]:
punctuations = [':', '،', '.', ')', '(', '}', '{', '؟', '!', '-', '/', '؛', '#', '*', '\n', '\"',
                ']', '[', '«', '»', '٪', '+', '٠', '\\', '\"', '_', '\'']


In [5]:
for row in tqdm(sheet.iter_rows()):
    each_doc_vector = {}
    line = row[1].value
    if row[0].value == 'id':
        continue
    if row[1].value == '':
        continue
    N_documents += 1
    line = normalizer.normalize(line)
    for p in punctuations:
        if p in line:
            line = line.replace(p, " ")
    extracted_tokens = word_tokenize(line)
    stem_tokens = []
    for t in extracted_tokens:
        stem_tokens.append(stemmer.stem(t))

    term_doc = []
    for w in stem_tokens:
        term_doc.append({'term': w, 'doc_id': N_documents})
    tokens.extend(term_doc)
    
    for t in stem_tokens:
        each_doc_vector[t] = each_doc_vector.get(t, 0) + 1
    doc_tf[N_documents] = collections.OrderedDict(sorted(each_doc_vector.items()))
    each_w = {}
    for term, tf in doc_tf[N_documents].items():
        each_w[term] = (1+math.log(tf, 10))
    doc_vectors[N_documents] = each_w
    c = ""
    if row[2].value == "political":
        c = "politics"
    elif row[2].value == "sports":
        c = "sport"
    else:
        c = row[2].value
    doc_classes[N_documents] = c
    links[N_documents] = row[3].value

11438it [00:20, 560.40it/s]


In [6]:
xlsx_file = Path('IR00_3_17k News.xlsx')
wb_obj = openpyxl.load_workbook(xlsx_file)
sheet = wb_obj.active

In [7]:
for row in tqdm(sheet.iter_rows()):
    each_doc_vector = {}
    line = row[1].value
    if row[0].value == 'id':
        continue
    if row[1].value == '':
        continue
    N_documents += 1
    line = normalizer.normalize(line)
    for p in punctuations:
        if p in line:
            line = line.replace(p, " ")
    extracted_tokens = word_tokenize(line)
    stem_tokens = []
    for t in extracted_tokens:
        stem_tokens.append(stemmer.stem(t))

    term_doc = []
    for w in stem_tokens:
        term_doc.append({'term': w, 'doc_id': N_documents})
    tokens.extend(term_doc)
    
    for t in stem_tokens:
        each_doc_vector[t] = each_doc_vector.get(t, 0) + 1
    doc_tf[N_documents] = collections.OrderedDict(sorted(each_doc_vector.items()))
    each_w = {}
    for term, tf in doc_tf[N_documents].items():
        each_w[term] = (1+math.log(tf, 10))
    doc_vectors[N_documents] = each_w
    c = ""
    if row[2].value == "political":
        c = "politics"
    elif row[2].value == "sports":
        c = "sport"
    else:
        c = row[2].value
    doc_classes[N_documents] = c
    links[N_documents] = row[3].value

17965it [00:52, 344.15it/s]


In [8]:
xlsx_file = Path('IR00_3_20k News.xlsx')
wb_obj = openpyxl.load_workbook(xlsx_file)
sheet = wb_obj.active

In [10]:
for row in tqdm(sheet.iter_rows()):
    each_doc_vector = {}
    line = row[1].value
    if row[0].value == 'id':
        continue
    if row[1].value == '':
        continue
    N_documents += 1
    line = normalizer.normalize(line)
    for p in punctuations:
        if p in line:
            line = line.replace(p, " ")
    extracted_tokens = word_tokenize(line)
    stem_tokens = []
    for t in extracted_tokens:
        stem_tokens.append(stemmer.stem(t))

    term_doc = []
    for w in stem_tokens:
        term_doc.append({'term': w, 'doc_id': N_documents})
    tokens.extend(term_doc)
    
    for t in stem_tokens:
        each_doc_vector[t] = each_doc_vector.get(t, 0) + 1
    doc_tf[N_documents] = collections.OrderedDict(sorted(each_doc_vector.items()))
    each_w = {}
    for term, tf in doc_tf[N_documents].items():
        each_w[term] = (1+math.log(tf, 10))
    doc_vectors[N_documents] = each_w
    c = ""
    if row[2].value == "political":
        c = "politics"
    elif row[2].value == "sports":
        c = "sport"
    else:
        c = row[2].value
    doc_classes[N_documents] = c 
    links[N_documents] = row[3].value

20661it [00:45, 451.12it/s]


### Dictionary-IDF

In [11]:
dictionary = {}
inverted_index = {}
idf = {}
doc_term_frq = []
for t in tqdm(tokens):
    word = t['term']
    doc_id = t['doc_id']
   
    doc_list = inverted_index.get(word, [])
    doc_list.append(doc_id)
    inverted_index[word] = doc_list
    
  

100%|██████████████████████████████████████████████████████████████████| 22309132/22309132 [00:34<00:00, 650879.05it/s]


In [12]:
inver_inex_dup = inverted_index.copy()
for i in inverted_index:
    inverted_index[i] = list(dict.fromkeys(inverted_index[i]))
inverted_index = collections.OrderedDict(sorted(inverted_index.items()))


In [13]:
for term in tqdm(inverted_index):
    df = len(inverted_index[term])
    idf[term] = math.log(N_documents / df, 10)
#     print(idf[term])

100%|██████████████████████████████████████████████████████████████████████| 174147/174147 [00:00<00:00, 904404.93it/s]


In [14]:
%%time

index_elimination_model = {}
for term in tqdm(inverted_index.keys()):
    index_elimination_model[term] = {}
    for doc in inverted_index[term]:
        index_elimination_model[term][doc] = doc_vectors[doc][term]


100%|████████████████████████████████████████████████████████████████████████| 174147/174147 [02:18<00:00, 1261.62it/s]

Wall time: 2min 18s






# Clustering


In [15]:
K = 100

In [16]:
%%time

leader_docid = []

while len(leader_docid) < K:
    new_leader = int(np.random.uniform(1, len(doc_vectors)))
    if new_leader not in leader_docid:
        leader_docid.append(new_leader)
leaders = []
for x in leader_docid:
    leaders.append(doc_vectors[x])


Wall time: 342 ms
Parser   : 163 ms


In [17]:
leader_l2 = [0]*len(leaders)
for i, leader in zip(range(len(leaders)), leaders):
    for t in leader.values():
        leader_l2[i] += t**2
print(leader_l2)

[229.31032151722528, 301.91531944129935, 129.1150308527137, 134.855874508451, 192.54958178636682, 257.1228674342035, 170.1195716869557, 514.2001118791259, 268.0626945190888, 223.08713144131875, 149.6914563009474, 870.6305224838185, 337.7090614702267, 63.128369204579805, 503.3043896365439, 210.92688898318664, 564.4661579287489, 212.29878795866094, 85.2232174693637, 65.45173768313859, 294.0290525190211, 204.05486605379272, 697.401623387854, 105.76209484738703, 318.0659452489258, 141.70265311274443, 174.21796097849605, 433.0619360318622, 151.8166076573797, 273.4473427636624, 356.9961638721993, 450.99921752147173, 306.16345399901985, 129.99746533753284, 131.98525287757337, 90.2789073335149, 227.44585340767125, 140.50791771318535, 104.1831919820591, 170.5778959374036, 92.1619407904094, 428.91891885407136, 91.79710459896906, 319.0269087858369, 76.46280122753382, 342.4389009729194, 164.06934829338437, 337.17501297508636, 268.770302402677, 211.36408120721455, 288.4741027967819, 169.81625219816

In [18]:
%%time
clusters = {}

for i in tqdm(range(len(doc_vectors))):
    doc = doc_vectors[i+1]
    similarity = []
    index = 0
    for leader in leaders:
        cosine = 0.0
        for term in doc.keys():
            doc_tf = doc.get(term, 0)
            leader_tf = leader.get(term, 0)
            if doc_tf == 0 or leader_tf == 0:
                continue
            cosine += doc_tf*(idf[term])*leader_tf
        cosine /= math.sqrt(leader_l2[index])
        similarity.append(cosine)
        index += 1
    cluster_list = clusters.get(similarity.index(max(similarity)), [])
    cluster_list.append(i+1)
    clusters[similarity.index(max(similarity))] = cluster_list


100%|███████████████████████████████████████████████████████████████████████████| 50061/50061 [05:08<00:00, 162.02it/s]

Wall time: 5min 8s
Compiler : 287 ms


In [19]:
for l, i in zip(range(len(leaders)), range(len(clusters))):
    print(f"{l} : {len(clusters[i])}")

0 : 551
1 : 1180
2 : 79
3 : 773
4 : 429
5 : 112
6 : 409
7 : 636
8 : 77
9 : 596
10 : 111
11 : 1703
12 : 139
13 : 116
14 : 1397
15 : 221
16 : 310
17 : 122
18 : 98
19 : 378
20 : 654
21 : 130
22 : 341
23 : 219
24 : 294
25 : 218
26 : 199
27 : 255
28 : 249
29 : 369
30 : 174
31 : 2485
32 : 121
33 : 115
34 : 550
35 : 275
36 : 428
37 : 62
38 : 166
39 : 147
40 : 49
41 : 31
42 : 160
43 : 161
44 : 78
45 : 754
46 : 774
47 : 555
48 : 161
49 : 386
50 : 264
51 : 219
52 : 957
53 : 112
54 : 5087
55 : 621
56 : 205
57 : 364
58 : 435
59 : 89
60 : 250
61 : 168
62 : 407
63 : 246
64 : 315
65 : 482
66 : 258
67 : 227
68 : 587
69 : 968
70 : 636
71 : 1221
72 : 281
73 : 1208
74 : 142
75 : 2815
76 : 320
77 : 146
78 : 1246
79 : 420
80 : 1395
81 : 609
82 : 663
83 : 1089
84 : 330
85 : 336
86 : 69
87 : 651
88 : 44
89 : 99
90 : 537
91 : 1771
92 : 34
93 : 359
94 : 79
95 : 146
96 : 250
97 : 203
98 : 384
99 : 320


In [20]:
%%time
iterations = 3
for it in range(iterations):
    leaders = []
    for i in range(K):
        vec = {}
        for d in clusters.get(i, []):
            doc = doc_vectors[d]
            for term in doc.keys():
                vec[term] = vec.get(term, 0) + doc[term]
        if len(clusters.get(i, [])) > 0:
            for term in vec.keys():
                vec[term] = vec.get(term, 0) / len(clusters[i])
        leaders.append(vec)


    leader_l2 = [0]*len(leaders)
    for i, leader in zip(range(len(leaders)), leaders):
        for t in leader.values():
            leader_l2[i] += t

    clusters = {}
    for i in tqdm(range(len(doc_vectors))):
        doc = doc_vectors[i+1]
        similarity = []
        index = 0
        for leader in leaders:
            cosine = 0.0
            for term in doc.keys():
                doc_tf = doc.get(term, 0)
                leader_tf = leader.get(term, 0)
                if doc_tf == 0 or leader_tf == 0:
                    continue
                cosine += doc_tf*(idf[term])*leader_tf
            
            if leader_l2[index] > 0:
                cosine /= math.sqrt(leader_l2[index])
            similarity.append(cosine)
            index += 1

        cluster_list = clusters.get(similarity.index(max(similarity)), [])
        cluster_list.append(i+1)
        clusters[similarity.index(max(similarity))] = cluster_list
#     for l, i in zip(range(len(leaders)), range(K)):
#         print(f"{l} : {len(clusters.get(i, []))}")

  3%|██▋                                                                         | 1746/50061 [00:14<07:18, 110.25it/s]


  7%|█████▏                                                                       | 3347/50061 [00:29<08:02, 96.80it/s]


 10%|███████▎                                                                     | 4771/50061 [00:45<08:52, 85.08it/s]


 12%|█████████▍                                                                   | 6160/50061 [01:00<08:06, 90.32it/s]


 15%|███████████▎                                                                 | 7394/50061 [01:16<08:33, 83.11it/s]


...

 95%|████████████████████████████████████████████████████████████████████████▎   | 47655/50061 [10:12<00:31, 76.16it/s]


 97%|█████████████████████████████████████████████████████████████████████████▉  | 48675/50061 [10:29<00:24, 57.67it/s]


 99%|███████████████████████████████████████████████████████████████████████████▌| 49745/50061 [10:45<00:05, 59.04it/s]


100%|███████████████████████████████████████████████████████████████████████████████████| 3/3 [32:51<00:00, 657.17s/it]

Wall time: 32min 51s


In [21]:
for l, i in zip(range(len(leaders)), range(K)):
    print(f"{l} : {len(clusters.get(i, []))}")

0 : 320
1 : 884
2 : 207
3 : 644
4 : 654
5 : 129
6 : 462
7 : 617
8 : 53
9 : 317
10 : 323
11 : 1524
12 : 401
13 : 270
14 : 504
15 : 405
16 : 592
17 : 350
18 : 255
19 : 191
20 : 268
21 : 802
22 : 147
23 : 301
24 : 321
25 : 206
26 : 333
27 : 286
28 : 621
29 : 546
30 : 202
31 : 2246
32 : 30
33 : 106
34 : 515
35 : 603
36 : 548
37 : 205
38 : 240
39 : 58
40 : 184
41 : 37
42 : 127
43 : 131
44 : 73
45 : 1211
46 : 802
47 : 1333
48 : 347
49 : 419
50 : 433
51 : 302
52 : 1147
53 : 262
54 : 4156
55 : 447
56 : 441
57 : 641
58 : 353
59 : 383
60 : 195
61 : 513
62 : 152
63 : 260
64 : 162
65 : 225
66 : 378
67 : 409
68 : 613
69 : 795
70 : 622
71 : 381
72 : 569
73 : 333
74 : 368
75 : 322
76 : 409
77 : 137
78 : 883
79 : 127
80 : 845
81 : 1855
82 : 412
83 : 1102
84 : 66
85 : 442
86 : 151
87 : 981
88 : 39
89 : 222
90 : 1056
91 : 278
92 : 1242
93 : 531
94 : 253
95 : 409
96 : 236
97 : 162
98 : 481
99 : 530


## File Writting

In [24]:
%%time
file = open('3doc_inverted_index.obj', 'wb') 
pickle.dump(inverted_index, file)
file.close()

Wall time: 1.33 s


In [25]:
%%time
file = open('3doc_idf.obj', 'wb') 
pickle.dump(idf, file)
file.close()

Wall time: 80.8 ms


In [26]:
%%time
file = open('3doc_leaders.obj', 'wb') 
pickle.dump(leaders, file)
file.close()

Wall time: 469 ms


In [27]:
%%time
file = open('3doc_doc_vectors.obj', 'wb') 
pickle.dump(doc_vectors, file)
file.close()

Wall time: 5.32 s


In [28]:
%%time
file = open('3doc_clusters.obj', 'wb') 
pickle.dump(clusters, file)
file.close()

Wall time: 150 ms


In [29]:
%%time
file = open('3doc_links.obj', 'wb') 
pickle.dump(links, file)
file.close()

Wall time: 2.01 s


In [30]:
%%time
file = open('3doc_index_elimination.obj', 'wb') 
pickle.dump(index_elimination_model, file)
file.close()

Wall time: 9.33 s


## File Reading

In [5]:
readed = open('3doc_inverted_index.obj', 'rb') 
inverted_index = pickle.load(readed)


readed = open('3doc_idf.obj', 'rb') 
idf = pickle.load(readed)

readed = open('3doc_leaders.obj', 'rb') 
leaders = pickle.load(readed)

readed = open('3doc_doc_vectors.obj', 'rb') 
doc_vectors = pickle.load(readed)

readed = open('3doc_clusters.obj', 'rb') 
clusters = pickle.load(readed)

readed = open('3doc_links.obj', 'rb') 
links = pickle.load(readed)

readed = open('3doc_index_elimination.obj', 'rb') 
index_elimination_model = pickle.load(readed)



# Query

In [13]:
query = input("Serach: ")
query = normalizer.normalize(query)
for p in punctuations:
    if p in query:
        query = query.replace(p, " ")
extracted_tokens = word_tokenize(query)
stem_tokens = []
for t in extracted_tokens:
    stem_tokens.append(stemmer.stem(t))


Serach: اعزام کاروان های اردوی راهیان نور


In [14]:
query_frq = {}
for t in stem_tokens:
    query_frq[t] = query_frq.get(t, 0) + 1
for term, tf in query_frq.items():
    query_frq[t] = 1+math.log(tf, 10)
print(query_frq)

{'اعزا': 1, 'کاروان': 1, 'اردو': 1, 'راه': 1, 'نور': 1.0}


In [15]:
%%time
leader_l2 = [0]*len(leaders)
for i, leader in zip(range(len(leaders)), leaders):
    for t in leader.values():
        leader_l2[i] += t**2
# print(leader_l2)

Wall time: 183 ms


In [16]:
%%time
result = {}
for leader in leaders:
    cosine = 0.0
    index = 0
    for term in query_frq.keys():
        q_tf = query_frq.get(term, 0)
        leader_tf = leader.get(term, 0)
        if q_tf == 0 or leader_tf == 0:
            continue
        cosine += leader_tf*(idf[term])*q_tf
#     print(leader_l2)
    cosine /= math.sqrt(leader_l2[index])
    index += 1
    if cosine > 0:
        result[leaders.index(leader)] = cosine
    
# print(result)

Wall time: 0 ns


In [17]:
%%time
b1 = 4
sorted_result = {k: v for k, v in sorted(result.items(), key=lambda item: item[1])}
sorted_result = dict(itertools.islice(reversed(sorted_result.items()), b1))
for leader_index in sorted_result.keys():
    print(leader_index)


15
9
36
81
Wall time: 995 µs


In [18]:
%%time
result = {}

for leader in sorted_result.keys():
    for doc in clusters[leader]:
        cosine = 0.0
        for term in query_frq.keys():
            q_tf = query_frq.get(term, 0)
            doc_tf = doc_vectors[doc].get(term, 0)
            if q_tf == 0 or doc_tf == 0:
                continue
            cosine += doc_tf*(idf[term])*q_tf
        doc_l2 = 0.0
        for t in doc_vectors[doc].values():
            doc_l2 += (1+math.log(t, 10))**2
        cosine /= math.sqrt(doc_l2)
        if cosine > 0:
            result[doc] = cosine

# print(result)

Wall time: 425 ms


In [19]:
b2 = 20
sorted_result = {k: v for k, v in sorted(result.items(), key=lambda item: item[1])}
sorted_result = dict(itertools.islice(reversed(sorted_result.items()), b2))
for doc in sorted_result.keys():
    for d, link in links.items():
        if d == doc:
            print(f"Document {doc} :\n{link}", end='\n__________________________________\n')


Document 8518 :
https://www.isna.ir/news/99070806230/۱۵-یادمان-دفاع-مقدس-به-عنوان-آثار-ملی-دفاع-مقدس-ثبت-شده-است
__________________________________
Document 9514 :
https://www.isna.ir/news/98010501105/مناطق-عملیاتی-خوزستان-هنوز-آلوده-به-مین-هستند
__________________________________
Document 10569 :
https://www.isna.ir/news/98072418585/نقش-خادمین-شهدا-در-برپایی-موکب-های-پذیرایی-از-زوار-حسینی
__________________________________
Document 24450 :
https://www.farsnews.ir/news/14000118000399/ممنوعیت-اعزام-کاروان‌های-غیرمجاز-عتبات-تا-پایان-فروردین-تمدید-شد
__________________________________
Document 9762 :
https://www.isna.ir/news/98022211759/اعلام-جزئیات-اعزام-کاروان-ویژه-جانبازان-به-سفر-حج-تمتع
__________________________________
Document 11265 :
https://www.isna.ir/news/98120504151/توقف-سفر-زمینی-به-عراق-تا-۲۰-اسفند-تعیین-وضعیت-اعزام-هوایی-تا
__________________________________
Document 3165 :
https://www.isna.ir/news/98120504151/توقف-سفر-زمینی-به-عراق-تا-۲۰-اسفند-تعیین-وضعیت-اعزام-هوایی-تا
__

# Classification

In [35]:
xlsx_file = Path('../IR_Spring2021_ph12_7k.xlsx')
wb_obj = openpyxl.load_workbook(xlsx_file)
sheet = wb_obj.active
new_doc_vectors = {}
new_classes = {}
tokens = []
new_links = {}

In [36]:
N_documents = 0
for row in sheet.iter_rows():
    each_doc_vector = {}
    line = row[1].value
    if row[1].value == '':
        continue
    if row[0].value == 'id':
        continue
#     if row[0].value > 100:
#         break
    N_documents += 1
    line = normalizer.normalize(line)
    for p in punctuations:
        if p in line:
            line = line.replace(p, " ")
    extracted_tokens = word_tokenize(line)
    stem_tokens = []
    for t in extracted_tokens:
        stem_tokens.append(stemmer.stem(t))

    term_doc = []
    for w in stem_tokens:
        term_doc.append({'term': w, 'doc_id': N_documents})
    tokens.extend(term_doc)
    
    for t in stem_tokens:
        each_doc_vector[t] = each_doc_vector.get(t, 0) + 1
    each_w = {}
    for t, w in each_doc_vector.items():
        each_w[t] = 1+math.log(w)
    new_doc_vectors[N_documents] = each_w
    new_links[N_documents] = row[2].value

In [44]:
K = 5
print(new_doc_vectors.keys())

dict_keys([1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219, 22

In [45]:
%%time

old_l2 = [0]*len(doc_vectors)
i = 0
for doc in tqdm(doc_vectors):
    for t in doc_vectors[doc].values():
        old_l2[i] += t**2
    i += 1

100%|███████████████████████████████████████████████████████████████████████████| 50061/50061 [01:18<00:00, 638.67it/s]

Wall time: 1min 18s


In [47]:
%%time
possible = {}
for doc in tqdm(new_doc_vectors):
    result = {}
    index = 0
    
    for term, new_tf in new_doc_vectors[doc].items():
        for old_doc, old_freq in index_elimination_model[term].items():
            wd = old_freq*(idf[term])
            wq = new_tf
            result[old_doc] = result.get(old_doc, 0) + (wd*wq)
 
    for r_doc in result.keys():
  
        l2_length = math.sqrt(old_l2[r_doc-1])
        result[r_doc] = result.get(r_doc, 0)/l2_length
    
    
    # List to hold values from dictionary
    heap_dict=[]
    # extract the values from dictionary
    for i in result.values():
        heap_dict.append(i)

    # heapify the values
    hq._heapify_max(heap_dict)   

    sorted_result = []
    while len(sorted_result) < K and len(heap_dict) > 0:
        value = hq._heappop_max(heap_dict)
        for key,val in result.items():
            if value == val and key not in sorted_result:
                sorted_result.append(key)
                break
    possible[doc] = sorted_result


100%|████████████████████████████████████████████████████████████████████████████| 7000/7000 [1:08:00<00:00,  1.72it/s]

Wall time: 1h 8min


In [49]:
# print(possible)

In [50]:
new_doc_classes = {}
for new_doc, val in tqdm(possible.items()):
    class_vec = {}
    for d in val:
        class_of_each_doc = doc_classes[d]
        class_vec[class_of_each_doc] = class_vec.get(class_of_each_doc, 0) + 1
    new_doc_classes[new_doc] = max(class_vec, key=class_vec.get)


100%|████████████████████████████████████████████████████████████████████████████| 7000/7000 [00:00<00:00, 7314.86it/s]


In [51]:
print(new_doc_classes)

{1: 'sport', 2: 'sport', 3: 'sport', 4: 'sport', 5: 'sport', 6: 'sport', 7: 'sport', 8: 'sport', 9: 'sport', 10: 'sport', 11: 'sport', 12: 'sport', 13: 'sport', 14: 'health', 15: 'sport', 16: 'sport', 17: 'sport', 18: 'sport', 19: 'sport', 20: 'culture', 21: 'sport', 22: 'sport', 23: 'sport', 24: 'sport', 25: 'sport', 26: 'sport', 27: 'sport', 28: 'sport', 29: 'sport', 30: 'sport', 31: 'sport', 32: 'sport', 33: 'sport', 34: 'sport', 35: 'sport', 36: 'sport', 37: 'sport', 38: 'sport', 39: 'sport', 40: 'sport', 41: 'sport', 42: 'sport', 43: 'culture', 44: 'sport', 45: 'sport', 46: 'sport', 47: 'sport', 48: 'sport', 49: 'sport', 50: 'sport', 51: 'sport', 52: 'sport', 53: 'sport', 54: 'sport', 55: 'sport', 56: 'sport', 57: 'sport', 58: 'sport', 59: 'sport', 60: 'sport', 61: 'sport', 62: 'sport', 63: 'sport', 64: 'politics', 65: 'sport', 66: 'sport', 67: 'sport', 68: 'sport', 69: 'health', 70: 'sport', 71: 'culture', 72: 'sport', 73: 'sport', 74: 'sport', 75: 'sport', 76: 'sport', 77: 'spor

In [52]:
classes = {}
for d, c in new_doc_classes.items():
    classes[c] = classes.get(c, 0) + 1

for c, f in classes.items():
    print(c, f)

sport 1672
health 1507
culture 198
politics 1625
economy 1998


In [11]:
%%time

new_inverted_index = {}
doc_term_frq = []
for t in tqdm(tokens):
    word = t['term']
    doc_id = t['doc_id']
    
    doc_list = new_inverted_index.get(word, [])
    doc_list.append(doc_id)
    new_inverted_index[word] = doc_list
    
    

100%|███████████████████████████████████████████████████████████████████| 2196732/2196732 [00:01<00:00, 1684105.58it/s]

Wall time: 1.36 s


In [12]:
%%time
# remove stop words
frq_sorted_dic = {k: v for k, v in sorted(new_inverted_index.items(), key=lambda item: item[1])}
new_stop_words = dict(itertools.islice(reversed(frq_sorted_dic.items()), 20))
for s in new_stop_words:
    new_inverted_index.pop(s)

Wall time: 107 ms


In [13]:
%%time

for i in new_inverted_index:
    new_inverted_index[i] = list(dict.fromkeys(new_inverted_index[i]))
new_inverted_index = collections.OrderedDict(sorted(new_inverted_index.items()))


Wall time: 213 ms


In [14]:
%%time
new_idf = {}
N_documents = len(new_doc_vectors)
for term in new_inverted_index:
    df = len(new_inverted_index[term])
    new_idf[term] = math.log(N_documents / df, 10)
    print(new_idf[term])

0.7537828803170339
3.5440680443502752
3.5440680443502752
3.8450980400142565
2.5663444390614276
3.5440680443502752
3.8450980400142565
3.8450980400142565
3.5440680443502752
3.8450980400142565
3.5440680443502752
3.1461280356782377
2.6690067809585756
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.5440680443502752
3.3679767852945943
2.1730001820785394
3.8450980400142565
1.947470948723815
2.6146491186359824
2.1549019599857426
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
2.2653144433974464
2.9999999999999996
2.1549019599857426
1.8813102126687014
2.6690067809585756
3.5440680443502752
3.8450980400142565
3.5440680443502752
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.84509804001

2.1638568026386693
3.3679767852945943
3.1461280356782377
3.5440680443502752
3.8450980400142565
3.243038048686294
3.8450980400142565
3.5440680443502752
3.8450980400142565
2.201645363528069
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
1.3022726130550768
2.9420080530223127
3.8450980400142565
2.765916793966632
2.447158031342219
3.8450980400142565
3.8450980400142565
3.8450980400142565
2.112704280191288
3.8450980400142565
3.243038048686294
3.8450980400142565
2.9999999999999996
3.5440680443502752
2.1461280356782377
3.5440680443502752
3.8450980400142565
3.3679767852945943
1.404188957949039
3.8450980400142565
2.0062489492770013
3.8450980400142565
0.9239319893765179
3.1461280356782377
3.8450980400142565
2.0816700464513196
3.5440680443502752
3.8450980400142565
2.8908555305749317
3.8450980400142565
3.1461280356782377
0.7235381958267558
3.066946789630613
2.73115468770742
2.397940008672037
3.5440680443502752
3.8450980400142565
3.8450980400142565
2.4301246920434387
3.24

2.112704280191288
3.8450980400142565
3.243038048686294
2.8450980400142565
3.8450980400142565
3.8450980400142565
3.243038048686294
2.8450980400142565
2.288795539246969
2.5228787452803374
3.8450980400142565
3.8450980400142565
3.1461280356782377
2.301029995663981
3.8450980400142565
2.0816700464513196
2.9999999999999996
2.9420080530223127
3.8450980400142565
3.5440680443502752
3.8450980400142565
2.8037053548560316
2.8450980400142565
3.066946789630613
3.5440680443502752
2.9420080530223127
3.8450980400142565
3.8450980400142565
1.3495537024678084
3.8450980400142565
3.5440680443502752
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.5440680443502752
1.4630809974393884
3.3679767852945943
3.8450980400142565
3.243038048686294
2.8450980400142565
3.1461280356782377
3.8450980400142565
2.5228787452803374
3.3679767852945943
3.5440680443502752
3.8450980400142565
3.3679767852945943
3.243038048686294
3.8450980400142565
2.2540334329877574
2.2653144433974464
3.8450980400142565
3.8450980400142565
3

3.8450980400142565
3.8450980400142565
3.5440680443502752
3.8450980400142565
3.5440680443502752
3.8450980400142565
1.134134921018981
3.8450980400142565
3.8450980400142565
3.5440680443502752
3.8450980400142565
1.8407766662316138
3.1461280356782377
2.6146491186359824
3.5440680443502752
3.3679767852945943
3.8450980400142565
3.8450980400142565
2.0125891273080203
2.765916793966632
3.3679767852945943
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
2.6146491186359824
3.1461280356782377
3.8450980400142565
1.7516763548520216
3.8450980400142565
2.765916793966632
3.243038048686294
2.73115468770742
2.8908555305749317
3.8450980400142565
3.1461280356782377
3.3679767852945943
3.8450980400142565
1.8628268069746883
3.3679767852945943
3.5440680443502752
3.5440680443502752
3.066946789630613
3.066946789630613
2.9999999999999996
3.5440680443502752
3.8450980400142565
3.1461280356782377
2.9420080530223127
3.5440680443502752
3.8450980400142565
3.8450980400142565
3.243038048686294
3.

2.9420080530223127
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.3679767852945943
3.8450980400142565
3.8450980400142565
3.3679767852945943
3.8450980400142565
2.288795539246969
1.2948696869591625
3.8450980400142565
3.8450980400142565
1.1183708309876845
1.8407766662316138
2.301029995663981
3.8450980400142565
3.5440680443502752
3.5440680443502752
2.0527063505160026
3.5440680443502752
2.1823402083326826
3.8450980400142565
1.8037053548560313
3.8450980400142565
2.413734275855269
3.1461280356782377
3.5440680443502752
2.089223184341765
3.8450980400142565
3.8450980400142565
0.8289006865018177
3.066946789630613
3.066946789630613
3.3679767852945943
3.5440680443502752
3.8450980400142565
3.8450980400142565
3.5440680443502752
3.5440680443502752
2.0190232373134305
1.8116742845273068
3.3679767852945943
3.8450980400142565
3.5440680443502752
2.9999999999999996
1.4852625576743688
3.8450980400142565
3.3679767852945943
2.447158031342219
3.8450980400142565
3.5440680443502752
3.3679767852945943


...

3.8450980400142565
3.5440680443502752
3.3679767852945943
3.5440680443502752
3.8450980400142565
3.3679767852945943
3.1461280356782377
3.5440680443502752
3.3679767852945943
3.5440680443502752
3.8450980400142565
3.3679767852945943
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.5440680443502752
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.5440680443502752
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.5440680443502752
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.243038048686294
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.3679767852945943
3.5440680443502752
3.8450980400142565
0.958607314841775
3.8450980400142565
2.8908555305749317
2.6146491186359824
3.8450980400142565
2.73115468770742
2.5898255349109505
2.353736346179984
3.3679767852945943
3.845098040014256

2.8908555305749317
3.8450980400142565
3.8450980400142565
2.191885526238913
3.8450980400142565
3.8450980400142565
3.5440680443502752
3.8450980400142565
3.8450980400142565
2.1461280356782377
3.1461280356782377
3.8450980400142565
3.5440680443502752
3.1461280356782377
2.9420080530223127
3.243038048686294
3.3679767852945943
3.066946789630613
3.8450980400142565
3.5440680443502752
3.3679767852945943
3.8450980400142565
3.8450980400142565
3.5440680443502752
3.5440680443502752
3.243038048686294
1.1638568026386695
2.4301246920434387
3.8450980400142565
3.8450980400142565
3.8450980400142565
1.6020599913279623
3.5440680443502752
1.8037053548560313
2.413734275855269
3.8450980400142565
3.5440680443502752
3.5440680443502752
3.8450980400142565
3.8450980400142565
2.2540334329877574
3.8450980400142565
3.8450980400142565
3.5440680443502752
3.3679767852945943
1.9156791142999638
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.3679767852945943
3.3679767852945943
3.8450980400142565
3.544068044350275

3.3679767852945943
3.3679767852945943
3.8450980400142565
3.3679767852945943
2.73115468770742
3.1461280356782377
3.1461280356782377
3.1461280356782377
3.3679767852945943
1.6329104356102988
3.5440680443502752
3.8450980400142565
3.243038048686294
3.8450980400142565
3.8450980400142565
2.5026753591920503
3.8450980400142565
3.8450980400142565
3.066946789630613
3.8450980400142565
3.8450980400142565
2.5440680443502752
3.8450980400142565
3.8450980400142565
3.8450980400142565
2.0969100130080562
3.243038048686294
3.1461280356782377
2.288795539246969
3.5440680443502752
3.3679767852945943
2.8908555305749317
3.8450980400142565
3.5440680443502752
2.9999999999999996
3.1461280356782377
2.1290946963794575
3.8450980400142565
2.5228787452803374
3.8450980400142565
3.3679767852945943
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.5440680443502752
3.3679767852945943
1.9817751798938008
3.8450980400142565
2.6690067809585756
3.8450980400142565
3.5440680443502752
3.8450980400142565
0.9975253808721446

3.243038048686294
2.765916793966632
3.8450980400142565
3.1461280356782377
3.8450980400142565
3.066946789630613
3.5440680443502752
3.8450980400142565
3.066946789630613
2.9420080530223127
1.9938396912951812
2.6989700043360183
3.5440680443502752
3.8450980400142565
3.066946789630613
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
2.9999999999999996
3.8450980400142565
2.8908555305749317
3.8450980400142565
2.9420080530223127
2.8908555305749317
3.066946789630613
3.8450980400142565
2.8908555305749317
3.8450980400142565
3.3679767852945943
3.066946789630613
3.8450980400142565
3.8450980400142565
3.8450980400142565
1.651973441659795
1.9208187539523751
2.8908555305749317
3.8450980400142565
3.243038048686294
3.8450980400142565
3.8450980400142565
3.066946789630613
3.8450980400142565
3.8450980400142565
3.243038048686294
3.8450980400142565
3.1461280356782377
3.8450980400142565
3.8450980400142565
3.8450980400142565
2.9420080530223127
2.9999999999999996
3.84

3.5440680443502752
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.1461280356782377
2.9420080530223127
3.5440680443502752
3.5440680443502752
3.5440680443502752
3.8450980400142565
3.5440680443502752
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.5440680443502752
3.8450980400142565
3.5440680443502752
3.8450980400142565
3.8450980400142565
3.5440680443502752
3.8450980400142565
3.8450980400142565
3.3679767852945943
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.243038048686294
3.3679767852945943
3.5440680443502752
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.5440680443502752
3.243038048686294
3.8450980400142565
3.8450980400142565
2.9999999999999996
3.3679767852945943
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.066946789630613
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.5440680443502752
3.8450980400142565
3.8450980400142565
3.8450980400142565
3.3679767852945943
3.8450980400142

In [59]:
%%time

new_index_elimination_model = {}
for term in tqdm(new_inverted_index.keys()):
    new_index_elimination_model[term] = {}
    for doc in new_inverted_index[term]:
        new_index_elimination_model[term][doc] = new_doc_vectors[doc][term]


100%|██████████████████████████████████████████████████████████████████████████| 34455/34455 [00:04<00:00, 7047.52it/s]

Wall time: 4.89 s


## File Writting

In [61]:
%%time
file = open('new_doc_vectors.obj', 'wb') 
pickle.dump(new_doc_vectors, file)
file.close()

file = open('new_index_elimination.obj', 'wb') 
pickle.dump(new_index_elimination_model, file)
file.close()

file = open('new_classes.obj', 'wb') 
pickle.dump(new_doc_classes, file)
file.close()

file = open('new_stop_words.obj', 'wb') 
pickle.dump(new_stop_words, file)
file.close()





Wall time: 1.11 s


In [ ]:
file = open('new_links.obj', 'wb') 
pickle.dump(new_links, file)
file.close()

In [15]:
file = open('new_idf.obj', 'wb') 
pickle.dump(new_idf, file)
file.close()

## File Reading

In [20]:
readed = open('new_doc_vectors.obj', 'rb') 
new_doc_vectors = pickle.load(readed)

readed = open('new_index_elimination.obj', 'rb') 
new_index_elimination_model = pickle.load(readed)

readed = open('new_classes.obj', 'rb') 
new_doc_classes = pickle.load(readed)

readed = open('new_stop_words.obj', 'rb') 
new_stop_words = pickle.load(readed)

readed = open('new_links.obj', 'rb') 
new_links = pickle.load(readed)

readed = open('new_idf.obj', 'rb') 
new_idf = pickle.load(readed)


# Query

In [52]:
%%time
query = input("Serach: ")
query_class = input("Class: ")
query = normalizer.normalize(query)
for p in punctuations:
    if p in query:
        query = query.replace(p, " ")
extracted_tokens = word_tokenize(query)
stem_tokens = []
for t in extracted_tokens:
    stem_tokens.append(stemmer.stem(t))
for s in new_stop_words:
    if s in stem_tokens:
        for t in stem_tokens:
            if t == s:
                stem_tokens.remove(t)

Serach: انقلاب
Class: culture
Wall time: 6.22 s


In [53]:
%%time
query_frq = {}
for t in stem_tokens:
    query_frq[t] = query_frq.get(t, 0) + 1
for term, tf in query_frq.items():
    query_frq[t] = 1+math.log(tf, 10)
print(query_frq)

{'انقلاب': 1.0}
Wall time: 0 ns


In [54]:
%%time
result = {}

for term in query_frq.keys():
    wq = 1+math.log(query_frq[term], 10)
    for doc in new_index_elimination_model[term].keys():
        if new_doc_classes[doc] == query_class:
            doc_tf = new_index_elimination_model[term].get(doc, 0)
            wd = doc_tf*(new_idf[term])
            result[doc] = result.get(doc, 0) + (wd*wq)
        
for doc in result.keys():
    l2_length = 0
    for t in new_doc_vectors[doc].values():
        l2_length += t**2
    l2_length = math.sqrt(l2_length)
    result[doc] = result.get(doc, 0)/l2_length
# print(result)

Wall time: 1.99 ms


In [55]:
K = 30

In [56]:
%%time
import heapq as hq
# List to hold values from dictionary
heap_dict=[]

# extract the values from dictionary
for i in result.values():
    heap_dict.append(i)
    
# heapify the values
hq._heapify_max(heap_dict)   

sorted_result = []
while len(sorted_result) < K and len(heap_dict) > 0:
    value = hq._heappop_max(heap_dict)
    for key,val in result.items():
        if value == val:
            if key not in sorted_result:
                sorted_result.append(key)
                break

Wall time: 0 ns


In [57]:
for doc in sorted_result:
    for d, link in new_links.items():
        if doc == d:
            print(f"Document {doc} :\n{link}", end='\n____________________________________________\n')
#             print(doc)

Document 3011 :
https://www.isna.ir/news/98082919290/نشست-بیانیه-گام-دوم-انقلاب-و-الزامات-ارتباطی-آن-برگزار-می-شود
____________________________________________
Document 903 :
https://www.isna.ir/news/99111108048/محمدرضا-طالقانی-خاطراتش-از-انقلاب-را-بازگو-می-کند
____________________________________________
Document 3057 :
https://www.isna.ir/news/98091914661/توطئه-های-دشمن-هر-روز-نظام-را-بر-سر-دوراهی-و-دغدغه-ها-قرار-می-دهد
____________________________________________
Document 3302 :
https://www.isna.ir/news/99020906760/اعتبار-۷۰-میلیاردی-توسعه-زیرساخت-های-گردشگری-روستاهای-استان-بوشهر
____________________________________________
Document 3038 :
https://www.isna.ir/news/98091309931/بسیج-برنامه-انتخاباتی-برای-مجلس-ندارد
____________________________________________
Document 2709 :
https://www.isna.ir/news/98041709012/تحلیل-مرحوم-آیت-الله-ربانی-املشی-از-امکان-وقوع-انقلاب-اسلامی
____________________________________________
Document 2498 :
https://www.isna.ir/news/99122821707/اعزام-نمایندگان-ر